In [ ]:
!pip install -U langchain-community langchain pypdf openai==0.28 tiktoken faiss-cpu faiss-gpu

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 50.6/50.6 kB 3.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.5/76.5 kB 7.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.4/2.4 MB 76.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 60.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 294.5/294.5 kB 25.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 59.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 27.5/27.5 MB 84.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 85.5/85.5 MB 27.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 407.7/407.7 kB 32.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 296.7/296.7 kB 25.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.4/76.4 kB 6.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.0/78.0 kB 6.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.5/49.5 

In [ ]:
!pip install datasets

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 472.7/472.7 kB 9.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 10.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 14.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 20.4 MB/s eta 0:00:00


In [ ]:
from langchain.document_loaders import PyPDFLoader
from langchain.vectorstores import FAISS
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.embeddings.openai import OpenAIEmbeddings
from langchain.llms import OpenAI, OpenAIChat
from langchain.chains import RetrievalQA
from langchain.prompts import PromptTemplate
import os

In [ ]:
OPENAI_API_KEY = "sk-KSe2I7IiZnza0P9iJziFera1Jmryp9ZRdY6mN8Pw_HT3BlbkFJebs3bjnaYjBFpYM26YWY1GT1y2ujHYk21bBRPnaRcA"

In [ ]:
pdf_folder = "/content"
pdf_files = [f for f in os.listdir(pdf_folder) if f.endswith('.pdf')]
documents = []

In [ ]:
os.environ["OPENAI_API_KEY"] = OPENAI_API_KEY

In [ ]:
all_documents = []
for pdf_path in pdf_files:
    loader = PyPDFLoader(pdf_path)
    documents = loader.load()
    all_documents.extend(documents)

In [ ]:
text_splitter = RecursiveCharacterTextSplitter(
    chunk_size=1000,
    chunk_overlap=100
)
split_docs = text_splitter.split_documents(all_documents)
embeddings = OpenAIEmbeddings()
vector_store = FAISS.from_documents(split_docs, embeddings)

In [ ]:
llm = OpenAIChat(model="gpt-3.5-turbo")
retriever = vector_store.as_retriever(search_type="similarity", search_kwargs={"k": 3})
qa_chain = RetrievalQA.from_chain_type(
    llm=llm,
    retriever=retriever,
    return_source_documents=True,
    chain_type="stuff"
)

/usr/local/lib/python3.10/dist-packages/langchain_community/llms/openai.py:1073: UserWarning: You are trying to use a chat model. This way of initializing it is no longer supported. Instead, please use: `from langchain_community.chat_models import ChatOpenAI`
  warnings.warn(


In [ ]:
def answer_question(query):
    response = qa_chain({"query": query})
    answer = response["result"]
    source_docs = response["source_documents"]
    print("\nAnswer:\n")
    print(answer)
    print("\nSources:\n")
    for i, doc in enumerate(source_docs):
        source_name = doc.metadata.get('source', 'Unknown Source')
        content_excerpt = doc.page_content[:500]
        print(f"Source {i + 1}: {source_name}\n")
        print(f"Content: {content_excerpt}...\n")
        print("-" * 50)

In [ ]:
user_query = "What are the main areas covered by the tea controlling act ? 2005"
answer_question(user_query)


Answer:

The main areas covered by the tea controlling act include regulation of tea estates and small holdings, establishment and operation of tea factories, conduct of tea auctions, sale and export of tea, marketing of tea, scientific research into tea production, and quality improvement.

Sources:

Source 1: Sri-Lanka-Tea-Board-Act-14-of-1975.pdf

Content: green tea leaf of estates and small 
holdings and for the manufacture of 
made tea or instant tea, 
(iii) the sums approved by the Board in 
order to provide advisory services 
to owners of estates and small 
holdings, to manufacturers of tea, 
and dealers in tea, and 
(iv) such expenses as may be incurred in 
connexion with Sri Lanka's 
membership of the International 
Part V1 of the Tea Control Act is repealed by Law No. 14 of 1975, (Sri Lanka Tea Board Law) now Chapter 
253 of this Edition....

--------------------------------------------------
Source 2: Sri-Lanka-Tea-Board-Act-14-of-1975.pdf

Content: charge of that Departmen

In [ ]:
import json
import os
import librosa
import numpy as np
from transformers import AutoTokenizer, AutoModelForCausalLM, TrainingArguments, Trainer
from datasets import Dataset
import torch
from transformers import TrainerCallback
import librosa
import torchaudio
from transformers import Wav2Vec2Processor, Wav2Vec2ForCTC

In [ ]:
audio_file_path = "Standardrecording5.mp3"
transcript = [
    {"start_time": "00:00", "speaker": "A", "text": "তুমি খোতা শুরু করো না"},
    {"start_time": "00:03", "speaker": "B", "text": "তুমি আমারে আইয়া ক্লাস ৪ হে দেখসিলায়, কিতা কিতা মনৌ আসে আমার ব্যাফারে, খৌও তো দেখি"},
    {"start_time": "00:09", "speaker": "A", "text": "আমি তোমার  ব্যাফারে, জে ছুটো শোময় একতু দুষ্টমী করতায় তোহ"},
    {"start_time": "00:12", "speaker": "B", "text": "দুষ্টমী তোহ আখোনো করি আমি"},
    {"start_time": "00:14", "speaker": "A", "text": "ছোটবেলায় দুষ্টামির একটা মাত্রা আছিল তোহ"},
    {"start_time": "00:17", "speaker": "B", "text": "মাত্রা কিতা আছিল ? কি কি দুষ্টমী খোরসি, মনে আসে নি, খৌও দেখি তো?"},
    {"start_time": "00:21", "speaker": "A", "text": "মনে আছে আমার, আমি তোমার কিতা করসি, ঐজে শোকলৌ উঠিয়া, রান্না টান্না করিয়া ভাত তাত খাওয়াইয়া দিতাম, তারপরে তুমি বাল্যসেবা দিতা, দিয়া শইরা তোমারে টুক টুকিত উঠাইয়া দিতাম, অনেক সময় স্কুল ও নিয়া যাইতাম, অনেক সময় তোমারে মাস্টার এর বাসায় নিয়া দিতাম, নাচের ক্লাস ও নিয়া যাইতাম আমি, তারপর তোমারে ঘরে নিয়া আসতাম"},
    {"start_time": "00:49", "speaker": "B", "text": "আয় আমার অৌখনও মনে আছে তুমি আমারে লইয়া জাইতায়, নন্দু ম্যাডাম এর স্কুল আর তারফর তুমি আর নীতা রে এপি স্যার এর ঘরে নিয়ে জাইতে আমার মনে আছে"},
    {"start_time": "01:01", "speaker": "A", "text": "লইয়া জাইতাম, লইয়া আইতাম"},
    {"start_time": "01:03", "speaker": "B", "text": "তারফর তুমি আমার স্কুলে তোহ নিয়া গেছোনা, একদিন অবশ্য গেছলায়, আমার ফাংশন আসলো আমার মনে আছে, তুমি গেছলায়, আর তারফর তুমি আমরার যা দুষ্টামি খরতাম, তোমার তো তুমি তো গিয়ে দিদি রে সব খইয়া দিতায়, আমি জানি"},
    {"start_time": "01:25", "speaker": "A", "text": "দুষ্টামি না খোরলে যীদি না খোইতাম তাইলে তোহ তোমারে কন্ট্রোল করতে ফারতাম না,  হের লাইগা দিদি রে কিছু শুনাইতাম যে দেখো দিদি নোনা এ দুষ্টুমি খোরের"},
    {"start_time": "01:34", "speaker": "B", "text": "ইটা ঠিক, তখন তুমি যখন আইছিলা তখন তুমি আমারে এতটুকু ফাঁসো এর ফরে রেবা মাসি ও আইছিলো, আমার মনে আছে, রেবা মাসি তো টিকতে ফারলাইন না,  অোখোনো সেদিন আমি দেখছি রেবা মাসিরে"},
    {"start_time": "01:47", "speaker": "A", "text": "তারফরে রেবা গেল, রেবা যাওয়ার ফোরতিকা আমি যে তোমারে ছোট ফাঁসলাম, ছোট তিকা তো তুমি এখন বাইশ-এ বয়সের হইয়া গেছো, অনেক বুঝদার হইয়া গেছো"},
    {"start_time": "01:55", "speaker": "B", "text": "না বাইশ বছর আর হইসি না, বিশ বছর হইসি আমি অফন, ঐত্ত কয় দিন ফরে আমি বড় হইবার ফরে আমি গুৱাহাটী গেলাম, আমার আগে তো দিদিভাই গেলগিয়া।  তুমি আমারে খয়ও তো দেখি, দিদিভাই রে তুমি কিতা পাইছ আয়িয়া, কিলা ফাইছ আর আমারে কিলা ফাইছ?"},
    {"start_time": "02:15", "speaker": "A", "text": "না মানে, দু'জনের মইধ্যে তফাত তফাত আছে, বলতে কুটু একটু মেচিউরড লেভেলে আছে বুঝছো আর নোনা যে ছোট সেই ছোটটার মতোই রইছে কিছু ফরিবর্তন হয়ছে না"},
    {"start_time": "02:28", "speaker": "B", "text": "আর কীতা জানো নী মানে, দিদিভাই কিছুটা ফাইসে আমার বাফের টা ফাইসে, আমি কীতা ফাইসি, মা এর ছটর পটর জিনিসটা ফাইসি, আর কীতা হইলো, দিদিভাই ফাইসে বাফের শান্ত প্রকৃতি টা আর আমি ফাইসি মা এর ছটর পটর প্রকৃতি, যা হোক গিয়া, দিদিভাই অত জলাইসে না কিন্তু একটু গিয়া টিভি দেখতো, একটু চিপস খাইতো, ওইটা আমার মধ্যে ও আসলো, আর আমি ওইটা করতাম, আমি গিয়া খই দিতাম মা রে, তোমার মনে আছে কিনা জানি না, আমার ঠিক মনে আছে।"},
    {"start_time": "03:10", "speaker": "A", "text": "কিন্তু তুমি ছোটবেলা ঠিক আছে লুকায় লুকায় কাজ গুলা করতায়, চিপস খাইতায়, বিস্কুট খাইতায়, ওটা খাইতায়, সেটা খাইতায়, ঠিক আছে মানিয়া নেওয়া গেছে, কিন্তু অোখনো তুমি যেই আগের, আগের যে আগের ও নোনা রইছ, কোনো ফরিবর্তন হয়নাই, ঐ ম্যাচুরিটি লেভেলটা আইসে না।"},
    {"start_time": "03:24", "speaker": "B", "text": "আসলে কি তা জানো নী, আমি অমনকি আমার স্কুল আর তারা বন্ধুয়েই খইসে যে সত্যি খইসে যে তৃষিতা তুই চেঞ্জ হইসস না, আমরা সবাই চেঞ্জ হই গেছি, সেইদিন আমি অনিশার লগে দুর্গা পূজায় গেছিলাম, অনিশা উঠিয়া খয়, তৃষিতা তুই আগের মতন রইসস, অখনও চেঞ্জও হস নাই, খিলা রে, আমি খইছি যে আমি চেঞ্জ তো হইছি না, ফালটাইসি না, কেনকি আমি ওরা ও আসি, আমার ওলা ও আসি, আমি মুখোশ ফরতে ফারতাম না, মুখোশ যারা ফরে, তারা ভাবে কিতা, কিতা ভাবে।"},
    {"start_time": "04:00", "speaker": "A", "text": "মানে কিছু মুখোশ যারা ফরে, তারা কিতা মানে বুঝদার, বেশি বুঝদার।"},
    {"start_time": "04:09", "speaker": "B", "text": "সামনে এক সেহরা, ফিছে এক সেহরা, আমি ওটা রাখতে ফারি, আমি খই দিছি অনিশা রে উঠিয়া আমি সামনে এক সেহরা আর পিছে এক সেহরা রাখতে ফারতাম না, আমার যেগু সেহরা, সামনে উ"},
    {"start_time": "04:18", "speaker": "A", "text": "অরখম থাকা টা আমার মতে বালা, বাইচ্চা বাইচ্চার মতে থাকলে বালা, বেশি ম্যাচিউরড লেভেল আইয়া শারলে প্রবলেম হইয়া যায়, অসুবিধা হইয়া যায়।"},
    {"start_time": "04:25", "speaker": "B", "text": "আসলে, আমার চোখের সামনে তুমি নিতারে দেখছো, আমি এত ফ্রেন্ডস আসলাম, তোহ নিতারে আমি কিতা দেখসি, আমার চোখের সামনে চেঞ্জ হইয়া গেছে, আমি ভাবতে ও ফারলাম না, আমার লগে যাইতো স্যারের বাড়ি, এক লগে আইতাম ঘরো, অখন ত্রিশিতা করিয়া সিনেও না, ঔইটা অবশ্য ঠিক কেউ কারো এই দুনিয়াত মনে রাখে না, কেউ কারো লগে থাকেও না খায় ও না ফরে ও না, আমি না খাওয়াইরাম তারে, না পরাইরাম তারে, ইটা তো খুনো খতা না, কিন্তু ইকটু মনে রাখতে ফারতো তো ত্রিশিতারে, ছোট বেলার তিকা বড় হয়েছি, তার বাবা যখন গেলো গিয়া আমি আসলাম তার লগে, আর কোনো কেউ ক্লাসত আসলো না, ইটা মনে রাখার খতা নানী গো।"},
    {"start_time": "05:00", "speaker": "A", "text": "কিন্তু ব্যাফারটা হইছে বাবা গেছে কি না গেছে ইটা তো মাতিয়া লাভ নাই, অখন তুমরা ক্লাসমেট আসলেই তো, একসাথে সলা ফেরা করছো তো ইকটু ফরিবর্তন হইয়া গেছে হই যাওক, তাইর টা ছাড়ো অখন তোমারটা তুমি বাবো, আমি যেরখম বাইচ্চা, বাইচ্চার মতো, মা বাবার কাসে সবসময় বাইচ্চা থাকা বালা, বেশি বুদ্ধিমান হওয়াও বালা না।"},
    {"start_time": "05:27", "speaker": "B", "text": "কিন্তু না আমি ইটা একটা উদাহরণ দিরাম, যে খিলা একটা মানুষের ফরিবর্তন হয়ে দুনিয়াত, আমি চোখের সামনে ইগুরে দেখরাম আর ইগু বড় হইয়া কিতা হই জার, ইগু তো ফরিবর্তন টুকু অগু খইরাম।"},
    {"start_time": "05:46", "speaker": "A", "text": "তারফর বাইচ্চা, বাইচ্চার মতন থাকা তা বালা, আমার মতন বালা, মা বাবার যে সবসময় ফুলাফান বাইচ্চা উ থাকে।"},
    {"start_time": "05:55", "speaker": "B", "text": "আমি তোমারে আমার লাইফ তিকা, জীবন তিকা কয়টা উদাহরণ দিরাম, দিরাম হইলো গিয়া যে, যেমন রাজু দা, রাজু দা বড় মাইয়া ইগু ধরি লাও, ইগু বালা, বহুত বালা, না খোরাম না, কিন্তু সেইদিন আমার আর কুড়ুলি দিদি রে আয়া খোর যে 'দিদি তোমরা খিতা, তোমরা তো দেখি তো খাবা বেশি খাই লাও', আমারে উঠিয়া খোর, অত বাচ্চা টুকু আমায়ে উঠিয়া খোর, তুমি একটু বেশি খাই লাইরায়, ইতা শিক্ষা, ঘরর শিক্ষার মাইনোত্তা রাখতে লাগে, ঘরো যেটা শিখায় বাচ্চারা ওটাও গিয়া ধরে, ওটাও বাইরে গিয়া ছাড়ে। বাচ্চা রার মন পরিষ্কার, তারা কিতা নিটো, তারা কিতা খাইতো, তারা বুঝে না, তারা যেটা নিবো, হেইটা গিয়া বাইরে ছাড়বো, অলা আমারে গিয়া সেইদিন রাজু দা'র মাইয়া গিয়া কয় 'দিদি তুমি তো কত মুটো হইয়া গেছ আর খাইরা নি তুমি, তোমার মা তোমারে না করছে না খাইতে না'। ইটা কি ঠিক একটা বাচ্চার লিগা কথা খওয়া ?"},
    {"start_time": "06:49", "speaker": "A", "text": "না ঠিক আছে, এরখম শিক্ষা দেওয়াটা ঠিক না, বুঝছ খোতা, ফুলাফান এ ফুলাফানের মতোই শিক্ষা দিয়ে উঠাইতে লাগে, একটা সময় আসে, যেমন শোলো শত্রু বছর এ ফড়লে ফরে, একটা শিক্ষা যে না এখন তো তুমি ছোট না এখন তো তুমি আস্তে আস্তে বড় হইতে আসো তখন বড়র শিক্ষাটা তারে শিখাইতে লাগে যে না ওইভাবে চলিও ইটা অন্যরকম করলে বালা হইব, ওটাই শিখাইতে লাগে। যেমন বাইরের মানুষরে ফট করি মুটা হই গেছে, এই হইছে, এই সব জিনিস খয়া ঠিক না।"},
    {"start_time": "07:13", "speaker": "B", "text": "আর, আমার মা আমারে যা শিক্ষা দিছে, ইটার তিকা ইটা বুঝা যায় বা বুঝি আমি অখনো, যেটা জ্ঞান আমি নিই, ঐটা তিকা ঐটাই হইল গিয়া। মানুষ এর ফিট ফিসে মাতে তে লাগে না, আর ইগুলো হইল গিয়া যে মানুষ যে খোইবায় একদম সিধা খোইবায়। মানুষ এর মুখের উপরে খোইবায়, ফিট ফিসে আরেক খতা, সামনে আরেক খতা, ইটা আমার সলতো না। খতা হইল গিয়া যে যা খোয় বায় সামনে খোই বায় আর পরিষ্কার কথা খতা বায়। সাধারণত মাত মাতবায়, অত ঘুরিয়া পেঁচাইয়া মাত মাতাইয়া লাভ নাই।"},
    {"start_time": "07:42", "speaker": "A", "text": "না, ঠিক আছে, ঘুরিয়ে ফেচাইয়া মাতটা ঠিক হয় না, একটা সময় আসে মানুষের ঘুরিয়া ফেচাইয়া মাত আর, আর সবসময় মুখোশ ফড়তে নাই যে সামনে আইলে সামনের খতা সামনে খইতে লাগে, ফিছনে কইতে নাই।"},
    {"start_time": "07:54", "speaker": "B", "text": "মুখোশ ও আবার দুই রখমর মুখোশ আছে, আমার বাবা এ আমারে খইসে, এক রকম মুখোশ যেটা তোমার নিজে রাখতে লাগে, একটা রাখতে লাগে যেটা বাইরের মানুষ এর লাইগা, গিয়া মন খুলিয়া সব খই দিতায় না, যে জানো না আমরা ওই জমি কিনরাম, জানো না আমার মা অত সোনা কিনসে, ইটা কিতা খইতে লাগে না, যেটাও যেটাও প্রশ্ন করে, যেটাও প্রশ্ন করে, বাইরের মানুষ এর খুব আগ্রহ থাকে, খুব আগ্রহ থাকে যে তুমি যে তোমার খয়টা ঘর আছে খয়টা গাড়ি আছে, অনেক ইচ্ছা থাকে জানার, তখন একটা মুখোশ ফরে ফইরা থাকতে লাগে না রে আমি কিছু জানি না রে, তুই কিতা জানোস না, তুই কিতা খইতে, তোমার কী মনে হয় যে ইতা মুখোশ ফরিয়া থাকতে লাগে নী।"},
    {"start_time": "08:29", "speaker": "A", "text": "না, দুইটা মুখোশ আছে কিন্তু একটা ভিতরের মুখোশটা দেখাইতে নাই, বাইরেরটা দেখাইতে লাগে, মানুষের লগে অখন সলা ফিরা করতে হইলে বাইরের টা দেখাইতে লাগবো, ভিতরেরটা ভিতরে রাখতায়,ভিতরেরটা তুমি বাইরে গিয়া খোওয়া টা ঠিক নায় তো।"},
    {"start_time": "08:42", "speaker": "B", "text": "ওইটা ও খইরাম যে এখটা মুখোশ রাখতে লাগে যে বাইরের মানুষ এর লাইগা জেইরা খুব খাতরনাক মানুষ যারা, সবসময় এহ ফোরিয়া থাকে যে আম্রার পরিবারর ক্ষতি খরতো কেনকি অখন কলি যুগ যা যুগ হইসে যে কেউ কারো বালা সায় না, শবে শবায়ের ক্ষতি সায়, ইতার লাইগা অখন মুখোশ ফোরাটা খুবই দরকার, কয় জনে মানুষ এর সামনে মুখোশ ফোরিয়া থাকতে লাগে যে নিজের জীবনো বাঁচা যায় যত ফারা যায় ঝগড়া ঝাটি এর থিকা দূর থাকতে লাগে, ঝগড়া ঝাটি ও খারাফ করি দেই জীবন রে।"}
]

In [ ]:
formatted_dialogues = []
conversation_id = "sylheti_conv_001"
dataset_path = "./sylheti_conversational_dataset.jsonl"
model_name = "csebuetnlp/banglabert"

In [ ]:
for idx, segment in enumerate(transcript):
    turn = {
        "conversation_id": conversation_id,
        "turn": idx + 1,
        "speaker": segment["speaker"],
        "text": segment["text"]
    }
    formatted_dialogues.append(turn)

In [ ]:
with open(dataset_path, "w", encoding="utf-8") as f:
    for dialogue in formatted_dialogues:
        f.write(json.dumps(dialogue, ensure_ascii=False) + "\n")

In [ ]:
def load_dataset(jsonl_file_path):
    return Dataset.from_json(jsonl_file_path)

In [ ]:
sylheti_dataset = load_dataset(dataset_path)

Generating train split: 0 examples [00:00, ? examples/s]

In [ ]:
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name)

/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(
If you want to use `ElectraForCausalLM` as a standalone, add `is_decoder=True.`
Some weights of ElectraForCausalLM were not initialized from the model checkpoint at csebuetnlp/banglabert and are newly initialized: ['generator_lm_head.bias', 'generator_predictions.LayerNorm.bias', 'generator_predictions.LayerNorm.weight', 'generator_predictions.dense.bias', 'generator_predictions.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [ ]:
def tokenize_data(example):
    return tokenizer(example["text"], truncation=True, padding="max_length", max_length=128)

In [ ]:
sylheti_tokenized_dataset = sylheti_dataset.map(tokenize_data, batched=True)

In [ ]:
class CustomTrainer(Trainer):
    def compute_loss(self, model, inputs, return_outputs=False):
        """
        Custom loss function to calculate the cross-entropy loss.
        """
        labels = inputs.pop("labels")  # Assuming 'labels' are present in your dataset
        outputs = model(**inputs)
        logits = outputs.logits
        loss_fct = torch.nn.CrossEntropyLoss()
        loss = loss_fct(logits.view(-1, logits.size(-1)), labels.view(-1))
        return (loss, outputs) if return_outputs else loss

In [ ]:
training_args = TrainingArguments(
    output_dir="./results",
    run_name="sylheti_fine_tune_run",
    num_train_epochs=3,
    per_device_train_batch_size=4,
    save_steps=10_000,
    save_total_limit=2,
    logging_dir="./logs",
)


trainer = CustomTrainer(
    model=model,
    args=training_args,
    train_dataset=sylheti_tokenized_dataset,
)

In [ ]:
trainer.train()

KeyError: 'labels'

In [ ]:
transcript_segments = [
    {"speaker": "A", "text": "তুমি খোতা শুরু করো না"},
    {"speaker": "B", "text": "তুমি আমারে আইয়া ক্লাস ৪ হে দেখসিলায়, কিতা কিতা মনৌ আসে আমার ব্যাফারে, খৌও তো দেখি"},
    {"speaker": "A", "text": "আমি তোমার  ব্যাফারে, জে ছুটো শোময় একতু দুষ্টমী করতায় তোহ"},
    {"speaker": "B", "text": "দুষ্টমী তোহ আখোনো করি আমি"},
    {"speaker": "A", "text": "ছোটবেলায় দুষ্টামির একটা মাত্রা আছিল তোহ"},
    {"speaker": "B", "text": "মাত্রা কিতা আছিল ? কি কি দুষ্টমী খোরসি, মনে আসে নি, খৌও দেখি তো?"},
    {"speaker": "A", "text": "মনে আছে আমার, আমি তোমার কিতা করসি, ঐজে শোকলৌ উঠিয়া, রান্না টান্না করিয়া ভাত তাত খাওয়াইয়া দিতাম, তারপরে তুমি বাল্যসেবা দিতা, দিয়া শইরা তোমারে টুক টুকিত উঠাইয়া দিতাম, অনেক সময় স্কুল ও নিয়া যাইতাম, অনেক সময় তোমারে মাস্টার এর বাসায় নিয়া দিতাম, নাচের ক্লাস ও নিয়া যাইতাম আমি, তারপর তোমারে ঘরে নিয়া আসতাম"},
    {"speaker": "B", "text": "আয় আমার অৌখনও মনে আছে তুমি আমারে লইয়া জাইতায়, নন্দু ম্যাডাম এর স্কুল আর তারফর তুমি আর নীতা রে এপি স্যার এর ঘরে নিয়ে জাইতে আমার মনে আছে"},
    {"speaker": "A", "text": "লইয়া জাইতাম, লইয়া আইতাম"},
    {"speaker": "B", "text": "তারফর তুমি আমার স্কুলে তোহ নিয়া গেছোনা, একদিন অবশ্য গেছলায়, আমার ফাংশন আসলো আমার মনে আছে, তুমি গেছলায়, আর তারফর তুমি আমরার যা দুষ্টামি খরতাম, তোমার তো তুমি তো গিয়ে দিদি রে সব খইয়া দিতায়, আমি জানি"},
    {"speaker": "A", "text": "দুষ্টামি না খোরলে যীদি না খোইতাম তাইলে তোহ তোমারে কন্ট্রোল করতে ফারতাম না,  হের লাইগা দিদি রে কিছু শুনাইতাম যে দেখো দিদি নোনা এ দুষ্টুমি খোরের"},
    {"speaker": "B", "text": "ইটা ঠিক, তখন তুমি যখন আইছিলা তখন তুমি আমারে এতটুকু ফাঁসো এর ফরে রেবা মাসি ও আইছিলো, আমার মনে আছে, রেবা মাসি তো টিকতে ফারলাইন না,  অোখোনো সেদিন আমি দেখছি রেবা মাসিরে"},
    {"speaker": "A", "text": "তারফরে রেবা গেল, রেবা যাওয়ার ফোরতিকা আমি যে তোমারে ছোট ফাঁসলাম, ছোট তিকা তো তুমি এখন বাইশ-এ বয়সের হইয়া গেছো, অনেক বুঝদার হইয়া গেছো"},
    {"speaker": "B", "text": "না বাইশ বছর আর হইসি না, বিশ বছর হইসি আমি অফন, ঐত্ত কয় দিন ফরে আমি বড় হইবার ফরে আমি গুৱাহাটী গেলাম, আমার আগে তো দিদিভাই গেলগিয়া।  তুমি আমারে খয়ও তো দেখি, দিদিভাই রে তুমি কিতা পাইছ আয়িয়া, কিলা ফাইছ আর আমারে কিলা ফাইছ?"},
    {"speaker": "A", "text": "না মানে, দু'জনের মইধ্যে তফাত তফাত আছে, বলতে কুটু একটু মেচিউরড লেভেলে আছে বুঝছো আর নোনা যে ছোট সেই ছোটটার মতোই রইছে কিছু ফরিবর্তন হয়ছে না"},
    {"speaker": "B", "text": "আর কীতা জানো নী মানে, দিদিভাই কিছুটা ফাইসে আমার বাফের টা ফাইসে, আমি কীতা ফাইসি, মা এর ছটর পটর জিনিসটা ফাইসি, আর কীতা হইলো, দিদিভাই ফাইসে বাফের শান্ত প্রকৃতি টা আর আমি ফাইসি মা এর ছটর পটর প্রকৃতি, যা হোক গিয়া, দিদিভাই অত জলাইসে না কিন্তু একটু গিয়া টিভি দেখতো, একটু চিপস খাইতো, ওইটা আমার মধ্যে ও আসলো, আর আমি ওইটা করতাম, আমি গিয়া খই দিতাম মা রে, তোমার মনে আছে কিনা জানি না, আমার ঠিক মনে আছে।"},
    {"speaker": "A", "text": "কিন্তু তুমি ছোটবেলা ঠিক আছে লুকায় লুকায় কাজ গুলা করতায়, চিপস খাইতায়, বিস্কুট খাইতায়, ওটা খাইতায়, সেটা খাইতায়, ঠিক আছে মানিয়া নেওয়া গেছে, কিন্তু অোখনো তুমি যেই আগের, আগের যে আগের ও নোনা রইছ, কোনো ফরিবর্তন হয়নাই, ঐ ম্যাচুরিটি লেভেলটা আইসে না।"},
    {"speaker": "B", "text": "আসলে কি তা জানো নী, আমি অমনকি আমার স্কুল আর তারা বন্ধুয়েই খইসে যে সত্যি খইসে যে তৃষিতা তুই চেঞ্জ হইসস না, আমরা সবাই চেঞ্জ হই গেছি, সেইদিন আমি অনিশার লগে দুর্গা পূজায় গেছিলাম, অনিশা উঠিয়া খয়, তৃষিতা তুই আগের মতন রইসস, অখনও চেঞ্জও হস নাই, খিলা রে, আমি খইছি যে আমি চেঞ্জ তো হইছি না, ফালটাইসি না, কেনকি আমি ওরা ও আসি, আমার ওলা ও আসি, আমি মুখোশ ফরতে ফারতাম না, মুখোশ যারা ফরে, তারা ভাবে কিতা, কিতা ভাবে।"},
    {"speaker": "A", "text": "মানে কিছু মুখোশ যারা ফরে, তারা কিতা মানে বুঝদার, বেশি বুঝদার।"},
    {"speaker": "B", "text": "সামনে এক সেহরা, ফিছে এক সেহরা, আমি ওটা রাখতে ফারি, আমি খই দিছি অনিশা রে উঠিয়া আমি সামনে এক সেহরা আর পিছে এক সেহরা রাখতে ফারতাম না, আমার যেগু সেহরা, সামনে উ"},
    {"speaker": "A", "text": "অরখম থাকা টা আমার মতে বালা, বাইচ্চা বাইচ্চার মতে থাকলে বালা, বেশি ম্যাচিউরড লেভেল আইয়া শারলে প্রবলেম হইয়া যায়, অসুবিধা হইয়া যায়।"},
    {"speaker": "B", "text": "আসলে, আমার চোখের সামনে তুমি নিতারে দেখছো, আমি এত ফ্রেন্ডস আসলাম, তোহ নিতারে আমি কিতা দেখসি, আমার চোখের সামনে চেঞ্জ হইয়া গেছে, আমি ভাবতে ও ফারলাম না, আমার লগে যাইতো স্যারের বাড়ি, এক লগে আইতাম ঘরো, অখন ত্রিশিতা করিয়া সিনেও না, ঔইটা অবশ্য ঠিক কেউ কারো এই দুনিয়াত মনে রাখে না, কেউ কারো লগে থাকেও না খায় ও না ফরে ও না, আমি না খাওয়াইরাম তারে, না পরাইরাম তারে, ইটা তো খুনো খতা না, কিন্তু ইকটু মনে রাখতে ফারতো তো ত্রিশিতারে, ছোট বেলার তিকা বড় হয়েছি, তার বাবা যখন গেলো গিয়া আমি আসলাম তার লগে, আর কোনো কেউ ক্লাসত আসলো না, ইটা মনে রাখার খতা নানী গো।"},
    {"speaker": "A", "text": "কিন্তু ব্যাফারটা হইছে বাবা গেছে কি না গেছে ইটা তো মাতিয়া লাভ নাই, অখন তুমরা ক্লাসমেট আসলেই তো, একসাথে সলা ফেরা করছো তো ইকটু ফরিবর্তন হইয়া গেছে হই যাওক, তাইর টা ছাড়ো অখন তোমারটা তুমি বাবো, আমি যেরখম বাইচ্চা, বাইচ্চার মতো, মা বাবার কাসে সবসময় বাইচ্চা থাকা বালা, বেশি বুদ্ধিমান হওয়াও বালা না।"},
    {"speaker": "B", "text": "কিন্তু না আমি ইটা একটা উদাহরণ দিরাম, যে খিলা একটা মানুষের ফরিবর্তন হয়ে দুনিয়াত, আমি চোখের সামনে ইগুরে দেখরাম আর ইগু বড় হইয়া কিতা হই জার, ইগু তো ফরিবর্তন টুকু অগু খইরাম।"},
    {"speaker": "A", "text": "তারফর বাইচ্চা, বাইচ্চার মতন থাকা তা বালা, আমার মতন বালা, মা বাবার যে সবসময় ফুলাফান বাইচ্চা উ থাকে।"},
    {"speaker": "B", "text": "আমি তোমারে আমার লাইফ তিকা, জীবন তিকা কয়টা উদাহরণ দিরাম, দিরাম হইলো গিয়া যে, যেমন রাজু দা, রাজু দা বড় মাইয়া ইগু ধরি লাও, ইগু বালা, বহুত বালা, না খোরাম না, কিন্তু সেইদিন আমার আর কুড়ুলি দিদি রে আয়া খোর যে 'দিদি তোমরা খিতা, তোমরা তো দেখি তো খাবা বেশি খাই লাও', আমারে উঠিয়া খোর, অত বাচ্চা টুকু আমায়ে উঠিয়া খোর, তুমি একটু বেশি খাই লাইরায়, ইতা শিক্ষা, ঘরর শিক্ষার মাইনোত্তা রাখতে লাগে, ঘরো যেটা শিখায় বাচ্চারা ওটাও গিয়া ধরে, ওটাও বাইরে গিয়া ছাড়ে। বাচ্চা রার মন পরিষ্কার, তারা কিতা নিটো, তারা কিতা খাইতো, তারা বুঝে না, তারা যেটা নিবো, হেইটা গিয়া বাইরে ছাড়বো, অলা আমারে গিয়া সেইদিন রাজু দা'র মাইয়া গিয়া কয় 'দিদি তুমি তো কত মুটো হইয়া গেছ আর খাইরা নি তুমি, তোমার মা তোমারে না করছে না খাইতে না'। ইটা কি ঠিক একটা বাচ্চার লিগা কথা খওয়া?"},
    {"speaker": "A", "text": "না ঠিক আছে, এরখম শিক্ষা দেওয়াটা ঠিক না, বুঝছ খোতা, ফুলাফান এ ফুলাফানের মতোই শিক্ষা দিয়ে উঠাইতে লাগে, একটা সময় আসে, যেমন শোলো শত্রু বছর এ ফড়লে ফরে, একটা শিক্ষা যে না এখন তো তুমি ছোট না এখন তো তুমি আস্তে আস্তে বড় হইতে আসো তখন বড়র শিক্ষাটা তারে শিখাইতে লাগে যে না ওইভাবে চলিও ইটা অন্যরকম করলে বালা হইব, ওটাই শিখাইতে লাগে। যেমন বাইরের মানুষরে ফট করি মুটা হই গেছে, এই হইছে, এই সব জিনিস খয়া ঠিক না।"},
    {"speaker": "B", "text": "আর, আমার মা আমারে যা শিক্ষা দিছে, ইটার তিকা ইটা বুঝা যায় বা বুঝি আমি অখনো, যেটা জ্ঞান আমি নিই, ঐটা তিকা ঐটাই হইল গিয়া। মানুষ এর ফিট ফিসে মাতে তে লাগে না, আর ইগুলো হইল গিয়া যে মানুষ যে খোইবায় একদম সিধা খোইবায়। মানুষ এর মুখের উপরে খোইবায়, ফিট ফিসে আরেক খতা, সামনে আরেক খতা, ইটা আমার সলতো না। খতা হইল গিয়া যে যা খোয় বায় সামনে খোই বায় আর পরিষ্কার কথা খতা বায়। সাধারণত মাত মাতবায়, অত ঘুরিয়া পেঁচাইয়া মাত মাতাইয়া লাভ নাই।"},
    {"speaker": "A", "text": "না, ঠিক আছে, ঘুরিয়ে ফেচাইয়া মাতটা ঠিক হয় না, একটা সময় আসে মানুষের ঘুরিয়া ফেচাইয়া মাত আর, আর সবসময় মুখোশ ফড়তে নাই যে সামনে আইলে সামনের খতা সামনে খইতে লাগে, ফিছনে কইতে নাই।"},
    {"speaker": "B", "text": "মুখোশ ও আবার দুই রখমর মুখোশ আছে, আমার বাবা এ আমারে খইসে, এক রকম মুখোশ যেটা তোমার নিজে রাখতে লাগে, একটা রাখতে লাগে যেটা বাইরের মানুষ এর লাইগা, গিয়া মন খুলিয়া সব খই দিতায় না, যে জানো না আমরা ওই জমি কিনরাম, জানো না আমার মা অত সোনা কিনসে, ইটা কিতা খইতে লাগে না, যেটাও যেটাও প্রশ্ন করে, যেটাও প্রশ্ন করে, বাইরের মানুষ এর খুব আগ্রহ থাকে, খুব আগ্রহ থাকে যে তুমি যে তোমার খয়টা ঘর আছে খয়টা গাড়ি আছে, অনেক ইচ্ছা থাকে জানার, তখন একটা মুখোশ ফরে ফইরা থাকতে লাগে না রে আমি কিছু জানি না রে, তুই কিতা জানোস না, তুই কিতা খইতে, তোমার কী মনে হয় যে ইতা মুখোশ ফরিয়া থাকতে লাগে নী।"},
    {"speaker": "A", "text": "না, দুইটা মুখোশ আছে কিন্তু একটা ভিতরের মুখোশটা দেখাইতে নাই, বাইরেরটা দেখাইতে লাগে, মানুষের লগে অখন সলা ফিরা করতে হইলে বাইরের টা দেখাইতে লাগবো, ভিতরেরটা ভিতরে রাখতায়,ভিতরেরটা তুমি বাইরে গিয়া খোওয়া টা ঠিক নায় তো।"},
    {"speaker": "B", "text": "ওইটা ও খইরাম যে এখটা মুখোশ রাখতে লাগে যে বাইরের মানুষ এর লাইগা জেইরা খুব খাতরনাক মানুষ যারা, সবসময় এহ ফোরিয়া থাকে যে আম্রার পরিবারর ক্ষতি খরতো কেনকি অখন কলি যুগ যা যুগ হইসে যে কেউ কারো বালা সায় না, শবে শবায়ের ক্ষতি সায়, ইতার লাইগা অখন মুখোশ ফোরাটা খুবই দরকার, কয় জনে মানুষ এর সামনে মুখোশ ফোরিয়া থাকতে লাগে যে নিজের জীবনো বাঁচা যায় যত ফারা যায় ঝগড়া ঝাটি এর থিকা দূর থাকতে লাগে, ঝগড়া ঝাটি ও খারাফ করি দেই জীবন রে।"}
]




In [ ]:
# Step 1: Data Preparation in JSONL Format

import json

def prepare_data_for_llm(transcript_segments):
    data = []
    conversation_id = "sylheti_conv_001"
    dialogue = []
    turn_counter = 1

    for segment in transcript_segments:
        dialogue.append({
            "turn": turn_counter,
            "speaker": segment['speaker'],
            "text": segment['text']
        })
        turn_counter += 1

    # Creating a conversation object
    conversation = {
        "conversation_id": conversation_id,
        "dialogue": dialogue
    }
    data.append(conversation)

    # Saving to JSONL format
    with open("sylheti_conversation_dataset.jsonl", "w", encoding='utf-8') as f:
        for entry in data:
            f.write(json.dumps(entry, ensure_ascii=False) + "\n")


# Preparing data for LLM
prepare_data_for_llm(transcript_segments)


# Step 2: Tokenization and Dataset Preparation for LLM Fine-Tuning

from transformers import AutoTokenizer
from torch.utils.data import Dataset

# Select Bengali pre-trained model tokenizer (for Sylheti adaptation)
tokenizer = AutoTokenizer.from_pretrained("sagorsarker/bangla-bert-base")

class SylhetiDataset(Dataset):
    def __init__(self, jsonl_file, tokenizer):
        self.data = []
        with open(jsonl_file, 'r', encoding='utf-8') as f:
            for line in f:
                conversation = json.loads(line)
                dialogue = conversation['dialogue']
                for turn in dialogue:
                    encoded_text = tokenizer(turn['text'], padding='max_length', truncation=True, max_length=128, return_tensors='pt')
                    self.data.append({
                        'input_ids': encoded_text['input_ids'].squeeze(0),
                        'attention_mask': encoded_text['attention_mask'].squeeze(0),
                        'labels': encoded_text['input_ids'].squeeze(0)  # Adding labels for causal LM
                    })

    def __len__(self):
        return len(self.data)

    def __getitem__(self, idx):
        return self.data[idx]

# Prepare the dataset
sylheti_dataset = SylhetiDataset("sylheti_conversation_dataset.jsonl", tokenizer)


# Step 3: Fine-Tuning the Bengali Pre-trained Model for Sylheti LLM

import torch
from transformers import AutoModelForCausalLM, Trainer, TrainingArguments

# Load pre-trained Bengali model
model = AutoModelForCausalLM.from_pretrained("sagorsarker/bangla-bert-base").to('cuda')

# Training arguments for fine-tuning
# training_args = TrainingArguments(
#     output_dir="./sylheti_llm_finetuned",
#     eval_strategy="epoch",
#     learning_rate=5e-5,
#     per_device_train_batch_size=2,
#     per_device_eval_batch_size=2,
#     num_train_epochs=3,
#     weight_decay=0.01,
#     save_total_limit=2,
# )
training_args = TrainingArguments(
    output_dir="./sylheti_llm_finetuned",
    eval_strategy="steps",
    logging_strategy="steps",  # Enable logging at each step
    logging_steps=10,          # Log every 10 steps
    learning_rate=5e-5,
    per_device_train_batch_size=2,
    per_device_eval_batch_size=2,
    num_train_epochs=10,
    weight_decay=0.01,
    save_total_limit=2,
    logging_dir='./logs',
)

class CustomCallback(TrainerCallback):
    def on_log(self, args, state, control, logs=None, **kwargs):
        print(f"Step {state.global_step}: {logs}")

# Trainer for model fine-tuning
# trainer = Trainer(
#     model=model,
#     args=training_args,
#     train_dataset=sylheti_dataset,
#     eval_dataset=sylheti_dataset[:10]  # Example evaluation dataset
# )
print(len(sylheti_dataset))
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=sylheti_dataset,
    eval_dataset=sylheti_dataset[:10],
    callbacks=[CustomCallback()]  # Include custom callback
)

# Begin the fine-tuning process
trainer.train()

# Save the fine-tuned model
trainer.save_model("./sylheti_llm_finetuned")


# Step 4: Evaluating the Fine-tuned Model

def generate_response(prompt, model, tokenizer):
    inputs = tokenizer(prompt, return_tensors="pt").to('cuda')
    output = model.generate(inputs['input_ids'], max_length=50, num_return_sequences=1)
    response = tokenizer.decode(output[0], skip_special_tokens=True)
    return response

# Example evaluation
generated_response = generate_response("বালা নী?", model, tokenizer)
print("Model Response: ", generated_response)


/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(
If you want to use `BertLMHeadModel` as a standalone, add `is_decoder=True.`


32


Step 10: {'loss': 7.0333, 'grad_norm': 12.14242172241211, 'learning_rate': 4.6875e-05, 'epoch': 0.625}
Step 10: {'eval_loss': 1.7253780364990234, 'eval_runtime': 0.1266, 'eval_samples_per_second': 79.014, 'eval_steps_per_second': 39.507, 'epoch': 0.625}
Step 20: {'loss': 2.6619, 'grad_norm': 8.097376823425293, 'learning_rate': 4.375e-05, 'epoch': 1.25}
Step 20: {'eval_loss': 1.096137285232544, 'eval_runtime': 0.1548, 'eval_samples_per_second': 64.595, 'eval_steps_per_second': 32.298, 'epoch': 1.25}
Step 30: {'loss': 2.7522, 'grad_norm': 8.34583568572998, 'learning_rate': 4.0625000000000005e-05, 'epoch': 1.875}
Step 30: {'eval_loss': 0.7152469158172607, 'eval_runtime': 0.1552, 'eval_samples_per_second': 64.43, 'eval_steps_per_second': 32.215, 'epoch': 1.875}
Step 40: {'loss': 1.2706, 'grad_norm': 6.111132621765137, 'learning_rate': 3.7500000000000003e-05, 'epoch': 2.5}
Step 40: {'eval_loss': 0.4233627915382385, 'eval_runtime': 0.1496, 'eval_samples_per_second': 66.831, 'eval_steps_per_s

In [ ]:
generated_response = generate_response("কিতা খবর আছে?", model, tokenizer)
print("Model Response: ", generated_response)

Model Response:  কিতা খবর আছে?


In [ ]:
def prepare_data_for_llm(audio_files, transcript_segments):
    data = []
    conversation_id = "sylheti_conv_001"
    dialogue = []
    turn_counter = 1

    # Loading the Wav2Vec2 model for speech-to-text
    processor = Wav2Vec2Processor.from_pretrained("facebook/wav2vec2-large-960h")
    model_asr = Wav2Vec2ForCTC.from_pretrained("facebook/wav2vec2-large-960h").to("cuda")

    # Process audio files to get transcriptions
    for audio_file in audio_files:
        waveform, sr = torchaudio.load(audio_file)

        # Move waveform to CPU for resampling
        waveform = waveform.to("cpu")

        # Resample if the sample rate is different from 16kHz
        if sr != 16000:
            resampler = torchaudio.transforms.Resample(orig_freq=sr, new_freq=16000)
            waveform = resampler(waveform)

        # Ensure the waveform is in the correct shape
        # wav2vec2 expects a 1D tensor, i.e., [number_of_samples]
        waveform = waveform.squeeze()

        # Move waveform to GPU for processing
        waveform = waveform.to("cuda")

        # Check if waveform has more than one channel and average if needed
        if len(waveform.shape) == 2:
            waveform = waveform.mean(dim=0)  # Convert to mono by averaging channels

        # Add batch dimension
        input_values = processor(waveform, return_tensors="pt", sampling_rate=16000).input_values.to("cuda")

        # Get logits from the model
        with torch.no_grad():
            logits = model_asr(input_values).logits

        # Get predicted ids
        predicted_ids = torch.argmax(logits, dim=-1)

        # Decode the predicted transcription
        transcription = processor.decode(predicted_ids[0])

        # Add transcription to the dialogue
        dialogue.append({
            "turn": turn_counter,
            "speaker": "A",  # Assume "A" for simplicity, or adapt as per context
            "text": transcription
        })
        turn_counter += 1

    # Adding manual transcription segments if available
    for segment in transcript_segments:
        dialogue.append({
            "turn": turn_counter,
            "speaker": segment['speaker'],
            "text": segment['text']
        })
        turn_counter += 1

    # Creating a conversation object
    conversation = {
        "conversation_id": conversation_id,
        "dialogue": dialogue
    }
    data.append(conversation)

    # Saving to JSONL format
    with open("sylheti_conversation_dataset.jsonl", "w", encoding='utf-8') as f:
        for entry in data:
            f.write(json.dumps(entry, ensure_ascii=False) + "\n")

In [ ]:


# Example usage with audio files and transcript segments
audio_files = ["/content/Standardrecording5.mp3"]  # Paths to audio files

# Preparing data for LLM
prepare_data_for_llm(audio_files, transcript_segments)


# Step 2: Tokenization and Dataset Preparation for LLM Fine-Tuning

from transformers import AutoTokenizer
from torch.utils.data import Dataset

# Select Bengali pre-trained model tokenizer (for Sylheti adaptation)
tokenizer = AutoTokenizer.from_pretrained("sagorsarker/bangla-bert-base")

class SylhetiDataset(Dataset):
    def __init__(self, jsonl_file, tokenizer):
        self.data = []
        with open(jsonl_file, 'r', encoding='utf-8') as f:
            for line in f:
                conversation = json.loads(line)
                dialogue = conversation['dialogue']
                for turn in dialogue:
                    encoded_text = tokenizer(turn['text'], padding='max_length', truncation=True, max_length=128, return_tensors='pt')
                    self.data.append({
                        'input_ids': encoded_text['input_ids'].squeeze(0),
                        'attention_mask': encoded_text['attention_mask'].squeeze(0),
                        'labels': encoded_text['input_ids'].squeeze(0)  # Adding labels for causal LM
                    })

    def __len__(self):
        return len(self.data)

    def __getitem__(self, idx):
        return self.data[idx]

# Prepare the dataset
sylheti_dataset = SylhetiDataset("sylheti_conversation_dataset.jsonl", tokenizer)


# Step 3: Fine-Tuning the Bengali Pre-trained Model for Sylheti LLM

from transformers import AutoModelForCausalLM, Trainer, TrainingArguments

# Load pre-trained Bengali model
model = AutoModelForCausalLM.from_pretrained("sagorsarker/bangla-bert-base").to('cuda')

# Training arguments for fine-tuning
training_args = TrainingArguments(
    output_dir="./sylheti_llm_finetuned_audio",
    eval_strategy="epoch",
    logging_strategy="steps",
    logging_steps=10,
    learning_rate=5e-5,
    per_device_train_batch_size=2,
    per_device_eval_batch_size=2,
    num_train_epochs=5,  # Increased the number of epochs for more training
    weight_decay=0.01,
    save_total_limit=2,
)

# Trainer for model fine-tuning
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=sylheti_dataset,
    eval_dataset=sylheti_dataset[:10]  # Example evaluation dataset
)

# Begin the fine-tuning process
trainer.train()

# Save the fine-tuned model
trainer.save_model("./sylheti_llm_finetuned_audio")


# Step 4: Evaluating the Fine-tuned Model

def generate_response(prompt, model, tokenizer):
    inputs = tokenizer(prompt, return_tensors="pt").to('cuda')
    output = model.generate(inputs['input_ids'], max_length=50, num_return_sequences=1)
    response = tokenizer.decode(output[0], skip_special_tokens=True)
    return response

# Example evaluation
generated_response = generate_response("কিতা খবর আছে?", model, tokenizer)
print("Model Response: ", generated_response)


Some weights of the model checkpoint at facebook/wav2vec2-large-960h were not used when initializing Wav2Vec2ForCTC: ['wav2vec2.encoder.pos_conv_embed.conv.weight_g', 'wav2vec2.encoder.pos_conv_embed.conv.weight_v']
- This IS expected if you are initializing Wav2Vec2ForCTC from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing Wav2Vec2ForCTC from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of Wav2Vec2ForCTC were not initialized from the model checkpoint at facebook/wav2vec2-large-960h and are newly initialized: ['wav2vec2.encoder.pos_conv_embed.conv.parametrizations.weight.original0', 'wav2vec2.encoder.pos_conv_embed.conv.parametrizations.weight.original1', 'wav2vec2.masked_spec_embed']
You s

Model Response:  কিতা খবর আছে? কি কি কি কি কি কি কি কি কি কি কি কি কি কি কি কি কি কি কি কি কি কি কি কি কি কি কি কি কি কি কি কি কি কি কি কি কি কি কি কি কি কি কি


In [ ]:
generated_response = generate_response("বালা আসো?", model, tokenizer)
print("Model Response: ", generated_response)

Model Response:  বালা আসো? বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা বালা


In [ ]:
!pip install gTTS

In [ ]:
import openai
from gtts import gTTS


In [ ]:

# Set up your OpenAI API key
openai.api_key = "sk-KSe2I7IiZnza0P9iJziFera1Jmryp9ZRdY6mN8Pw_HT3BlbkFJebs3bjnaYjBFpYM26YWY1GT1y2ujHYk21bBRPnaRcA"


In [ ]:
import openai
from gtts import gTTS
import os


def get_bengali_response(prompt):
    # Use OpenAI's language model to generate a response
    response = openai.ChatCompletion.create(
        model="gpt-3.5-turbo",  # Updated model to gpt-3.5-turbo
        messages=[
            {"role": "system", "content": "You are a helpful assistant."},
            {"role": "user", "content": prompt}
        ],
        max_tokens=150,
        temperature=0.7
    )
    return response.choices[0].message['content'].strip()

def generate_audio(text, language="bn"):
    # Use gTTS to generate audio from text
    tts = gTTS(text=text, lang=language, slow=False)
    audio_file = "output.mp3"
    tts.save(audio_file)
    os.system(f"start {audio_file}")  # For Windows; use "afplay" for Mac or "xdg-open" for Linux

def main():
    # Example Sylheti input
    sylheti_text = "তোমার কি অইব, আইজকা মেলা গরম।"

    # Create a prompt to help the model understand Sylheti
    prompt = (
        "This is a conversation in the Sylheti dialect of Bengali. Understand and respond accordingly.\n"
        f"Sylheti: \"{sylheti_text}\"\n"
        "Translation: \"What happened to you? It’s very hot today.\"\n"
        "Response:"
    )

    # Get the response from the language model
    response_text = get_bengali_response(prompt)
    print("Text Response:", response_text)

    # Generate audio from the response text
    generate_audio(response_text)

if __name__ == "__main__":
    main()


Text Response: "আরে হা, আমার ভালো আছে। আমি ওকা জাত আমেরিকা থেকে এসেছি এই গরম আজকে। তোমার কি কাজ করা থাকে?"


In [ ]:
!ls

drive  IndicWav2Vec  sample_data


In [ ]:
!mkdir /content/drive/MyDrive/ai4bharatIndicwav2vec

In [ ]:
%cd /content/drive/MyDrive/ai4bharatIndicwav2vec

/content/drive/MyDrive/ai4bharatIndicwav2vec


In [ ]:
!rm mucs/bengali/train/audio/*
!rm mucs/bengali/valid/audio/*
!rm mucs/bengali/train/transcription.txt
!rm mucs/bengali/valid/transcription.txt
!touch mucs/bengali/train/transcription.txt
!touch mucs/bengali/valid/transcription.txt

In [ ]:
!pip install kaggle

# Create a Kaggle folder to store the key
!mkdir -p ~/.kaggle

# Copy kaggle.json to the created folder
!cp kaggle.json ~/.kaggle/

# Change permissions of the file to read-only
!chmod 600 ~/.kaggle/kaggle.json

In [ ]:
!kaggle competitions download -c ben10

100% 6.43G/6.43G [05:35<00:00, 21.8MB/s]
100% 6.43G/6.43G [05:35<00:00, 20.6MB/s]


In [ ]:
!unzip ben10.zip -d ben10

Streaming output truncated to the last 5000 lines.
  inflating: ben10/ben10/16_kHz_train_audio/train_sylhet (1513).wav  
  inflating: ben10/ben10/16_kHz_train_audio/train_sylhet (1514).wav  
  inflating: ben10/ben10/16_kHz_train_audio/train_sylhet (1515).wav  
  inflating: ben10/ben10/16_kHz_train_audio/train_sylhet (1516).wav  
  inflating: ben10/ben10/16_kHz_train_audio/train_sylhet (1517).wav  
  inflating: ben10/ben10/16_kHz_train_audio/train_sylhet (1518).wav  
  inflating: ben10/ben10/16_kHz_train_audio/train_sylhet (1519).wav  
  inflating: ben10/ben10/16_kHz_train_audio/train_sylhet (152).wav  
  inflating: ben10/ben10/16_kHz_train_audio/train_sylhet (1520).wav  
  inflating: ben10/ben10/16_kHz_train_audio/train_sylhet (1521).wav  
  inflating: ben10/ben10/16_kHz_train_audio/train_sylhet (1522).wav  
  inflating: ben10/ben10/16_kHz_train_audio/train_sylhet (1523).wav  
  inflating: ben10/ben10/16_kHz_train_audio/train_sylhet (1524).wav  
  inflating: ben10/ben10/16_kHz_train_au

In [ ]:
import pandas as pd
import torchaudio
from transformers import Wav2Vec2Processor, Wav2Vec2ForCTC
import torch
import os
from torch.utils.data import Dataset
from transformers import TrainingArguments, Trainer
import json

/usr/local/lib/python3.10/dist-packages/torch_xla/__init__.py:202: UserWarning: `tensorflow` can conflict with `torch-xla`. Prefer `tensorflow-cpu` when using PyTorch/XLA. To silence this warning, `pip uninstall -y tensorflow && pip install tensorflow-cpu`. If you are in a notebook environment such as Colab or Kaggle, restart your notebook runtime afterwards.
  warnings.warn(


In [ ]:
!git clone https://github.com/AI4Bharat/IndicWav2Vec.git

Cloning into 'IndicWav2Vec'...
remote: Enumerating objects: 1943, done.
remote: Counting objects: 100% (148/148), done.
remote: Compressing objects: 100% (28/28), done.
remote: Total 1943 (delta 135), reused 120 (delta 120), pack-reused 1795 (from 1)
Receiving objects: 100% (1943/1943), 139.58 MiB | 13.39 MiB/s, done.
Resolving deltas: 100% (370/370), done.
Updating files: 100% (759/759), done.


In [ ]:
!pip install jiwer datasets

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 472.7/472.7 kB 37.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 12.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 14.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.1/3.1 MB 102.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 19.6 MB/s eta 0:00:00


In [ ]:
import torch
from datasets import load_dataset, Audio, Dataset
from transformers import Wav2Vec2ForCTC, Wav2Vec2Processor, TrainingArguments, Trainer
from jiwer import wer
import librosa

In [ ]:
data_path = "/content/drive/MyDrive/ai4bharatIndicwav2vec/ben10/ben10/16_kHz_train_audio/train.csv"
source_audio_path = "/content/drive/MyDrive/ai4bharatIndicwav2vec/ben10/ben10/16_kHz_train_audio/"

In [ ]:
df = pd.read_csv(data_path)

# Check if any value in the 'filename' column contains "valid" (case-insensitive)
contains_valid = df[df['file_name'].str.contains('valid', case=False)]

# If there are any rows containing "valid" in their filename, print them
if not contains_valid.empty:
    print("The following filenames contain 'valid':")
    print(contains_valid)
else:
    print("No filenames contain 'valid' in the 'filename' column.")

No filenames contain 'valid' in the 'filename' column.


In [ ]:
root_dir = "ben10/ben10/16_kHz_valid_audio"

# Iterate over all files in the directory
for filename in os.listdir(root_dir):
    # Check if the filename does not contain "sylhet"
    if "sylhet" not in filename.lower():
        # Construct the full file path
        file_path = os.path.join(root_dir, filename)

        # Delete the file
        if os.path.isfile(file_path):
            os.remove(file_path)
            print(f"Removed: {file_path}")

print("All non-Sylhet files have been removed.")

Removed: ben10/ben10/16_kHz_valid_audio/valid_barishal (1).wav
Removed: ben10/ben10/16_kHz_valid_audio/valid_barishal (10).wav
Removed: ben10/ben10/16_kHz_valid_audio/valid_barishal (100).wav
Removed: ben10/ben10/16_kHz_valid_audio/valid_barishal (101).wav
Removed: ben10/ben10/16_kHz_valid_audio/valid_barishal (102).wav
Removed: ben10/ben10/16_kHz_valid_audio/valid_barishal (103).wav
Removed: ben10/ben10/16_kHz_valid_audio/valid_barishal (104).wav
Removed: ben10/ben10/16_kHz_valid_audio/valid_barishal (105).wav
Removed: ben10/ben10/16_kHz_valid_audio/valid_barishal (106).wav
Removed: ben10/ben10/16_kHz_valid_audio/valid_barishal (11).wav
Removed: ben10/ben10/16_kHz_valid_audio/valid_barishal (12).wav
Removed: ben10/ben10/16_kHz_valid_audio/valid_barishal (13).wav
Removed: ben10/ben10/16_kHz_valid_audio/valid_barishal (14).wav
Removed: ben10/ben10/16_kHz_valid_audio/valid_barishal (15).wav
Removed: ben10/ben10/16_kHz_valid_audio/valid_barishal (16).wav
Removed: ben10/ben10/16_kHz_valid_

In [ ]:
import pandas as pd
import torchaudio
from transformers import Wav2Vec2ForCTC, Wav2Vec2Processor
from datasets import Dataset
import torch
from torch.utils.data import DataLoader
from transformers import Trainer, TrainingArguments
import os
from shutil import copy2

In [ ]:
destination_base_path = 'mucs/bengali/'

In [ ]:
!ls ben10/ben10/16_kHz_valid_audio | grep ".csv"

In [ ]:
df = pd.read_csv(data_path)
df['file_name'] = df['file_name'].str.replace(' ', '')
filtered_df = df[df['file_name'].str.contains('sylhet', case=False)]

# Save the filtered CSV if needed
filtered_csv_path = os.path.join(destination_base_path, 'filtered_train.csv')
filtered_df.to_csv(filtered_csv_path, index=False)

# Define destination folders
train_audio_path = os.path.join(destination_base_path, 'train/audio')
valid_audio_path = os.path.join(destination_base_path, 'valid/audio')

In [ ]:
filtered_df.shape

(2903, 3)

In [ ]:
train_df = filtered_df.sample(frac=0.8, random_state=42)
valid_df = filtered_df.drop(train_df.index)

In [ ]:
def process_data(df, audio_folder, transcript_file_path):
    with open(transcript_file_path, 'w') as transcript_file:
        for _, row in df.iterrows():
            filename = row['file_name']
            transcript = row['transcriptions']
            source_file_path = os.path.join(source_audio_path, filename)

            if os.path.exists(source_file_path):
                # Copy the audio file to the corresponding destination folder
                copy2(source_file_path, audio_folder)
                # Write to transcript.txt
                transcript_file.write(f"{os.path.basename(filename)} {transcript}\n")

In [ ]:
directory_path = "/content/drive/MyDrive/ai4bharatIndicwav2vec/ben10/ben10/16_kHz_train_audio"
for filename in os.listdir(directory_path):
    # Construct full file path
    old_file_path = os.path.join(directory_path, filename)

    # Remove spaces in the filename
    new_filename = filename.replace(" ", "")
    new_file_path = os.path.join(directory_path, new_filename)

    # Rename the file if necessary
    if old_file_path != new_file_path:
        os.rename(old_file_path, new_file_path)
        print(f'Renamed: "{old_file_path}" to "{new_file_path}"')

print("All files renamed successfully.")

Streaming output truncated to the last 5000 lines.
Renamed: "/content/drive/MyDrive/ai4bharatIndicwav2vec/ben10/ben10/16_kHz_train_audio/train_rangpur (945).wav" to "/content/drive/MyDrive/ai4bharatIndicwav2vec/ben10/ben10/16_kHz_train_audio/train_rangpur(945).wav"
Renamed: "/content/drive/MyDrive/ai4bharatIndicwav2vec/ben10/ben10/16_kHz_train_audio/train_rangpur (946).wav" to "/content/drive/MyDrive/ai4bharatIndicwav2vec/ben10/ben10/16_kHz_train_audio/train_rangpur(946).wav"
Renamed: "/content/drive/MyDrive/ai4bharatIndicwav2vec/ben10/ben10/16_kHz_train_audio/train_rangpur (947).wav" to "/content/drive/MyDrive/ai4bharatIndicwav2vec/ben10/ben10/16_kHz_train_audio/train_rangpur(947).wav"
Renamed: "/content/drive/MyDrive/ai4bharatIndicwav2vec/ben10/ben10/16_kHz_train_audio/train_rangpur (948).wav" to "/content/drive/MyDrive/ai4bharatIndicwav2vec/ben10/ben10/16_kHz_train_audio/train_rangpur(948).wav"
Renamed: "/content/drive/MyDrive/ai4bharatIndicwav2vec/ben10/ben10/16_kHz_train_audio/tra

In [ ]:
process_data(train_df, train_audio_path, os.path.join(destination_base_path, 'train/transcription.txt'))
process_data(valid_df, valid_audio_path, os.path.join(destination_base_path, 'valid/transcription.txt'))



In [ ]:
!pwd

/content/drive/MyDrive/ai4bharatIndicwav2vec


In [ ]:
!pip install fairseq

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.6/9.6 MB 112.9 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
  Preparing metadata (pyproject.toml) ... done
Requested omegaconf<2.1 from https://files.pythonhosted.org/packages/d0/eb/9d63ce09dd8aa85767c65668d5414958ea29648a0eec80a4a7d311ec2684/omegaconf-2.0.6-py3-none-any.whl (from fairseq) has invalid metadata: .* suffix can only be used with `==` or `!=` operators
    PyYAML (>=5.1.*)
            ~~~~~~^
Please use pip<24.1 if you need to use this version.
Requested omegaconf<2.1 from https://files.pythonhosted.org/packages/e5/f6/043b6d255dd6fbf2025110cea35b87f4c5100a181681d8eab496269f0d5b/omegaconf-2.0.5-py3-none-any.whl (from fairseq) has invalid metadata: .* suffix can only be used with `==` or `!=` operators
    PyYAML (>=5.1.*)
            ~~~~~~^
Please use pip<24.1 if you need to use this version.
Requested omegaconf<2.1 from htt

In [ ]:
!bash m_process.sh /content/drive/MyDrive/ai4bharatIndicwav2vec/mucs

/content/drive/MyDrive/ai4bharatIndicwav2vec/mucs/bengali
  0% 0/5 [00:00<?, ?it/s]Wavs:  ['/content/drive/MyDrive/ai4bharatIndicwav2vec/mucs/bengali/train/audio/train_sylhet(1126).wav', '/content/drive/MyDrive/ai4bharatIndicwav2vec/mucs/bengali/train/audio/train_sylhet(1753).wav', '/content/drive/MyDrive/ai4bharatIndicwav2vec/mucs/bengali/train/audio/train_sylhet(1440).wav', '/content/drive/MyDrive/ai4bharatIndicwav2vec/mucs/bengali/train/audio/train_sylhet(2573).wav', '/content/drive/MyDrive/ai4bharatIndicwav2vec/mucs/bengali/train/audio/train_sylhet(2099).wav', '/content/drive/MyDrive/ai4bharatIndicwav2vec/mucs/bengali/train/audio/train_sylhet(713).wav', '/content/drive/MyDrive/ai4bharatIndicwav2vec/mucs/bengali/train/audio/train_sylhet(2038).wav', '/content/drive/MyDrive/ai4bharatIndicwav2vec/mucs/bengali/train/audio/train_sylhet(912).wav', '/content/drive/MyDrive/ai4bharatIndicwav2vec/mucs/bengali/train/audio/train_sylhet(2611).wav', '/content/drive/MyDrive/ai4bharatIndicwav2vec/m

In [ ]:
%cd /content/drive/MyDrive/ai4bharatIndicwav2vec

/content/drive/MyDrive/ai4bharatIndicwav2vec


In [ ]:
!rm -rf fairseq

In [ ]:
!git clone https://github.com/facebookresearch/fairseq.git

Cloning into 'fairseq'...
remote: Enumerating objects: 35385, done.
remote: Counting objects: 100% (48/48), done.
remote: Compressing objects: 100% (35/35), done.
remote: Total 35385 (delta 10), reused 38 (delta 10), pack-reused 35337 (from 1)
Receiving objects: 100% (35385/35385), 25.47 MiB | 18.55 MiB/s, done.
Resolving deltas: 100% (25539/25539), done.
Updating files: 100% (1637/1637), done.


In [ ]:
%cd /content/drive/MyDrive/ai4bharatIndicwav2vec/fairseq

/content/drive/MyDrive/ai4bharatIndicwav2vec/fairseq


In [ ]:
%ls

CODE_OF_CONDUCT.md  fairseq/        LICENSE         RELEASE.md        setup.py
CONTRIBUTING.md     fairseq_cli/    MANIFEST.in     release_utils.py  tests/
docs/               hubconf.py      pyproject.toml  scripts/          train.py
examples/           hydra_plugins/  README.md       setup.cfg


In [ ]:
!pip install pip==23.0.1

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 22.2 MB/s eta 0:00:00
  Attempting uninstall: pip
    Found existing installation: pip 24.1.2
    Uninstalling pip-24.1.2:
      Successfully uninstalled pip-24.1.2


In [ ]:
#!git checkout cf8ff8c3c5242e6e71e8feb40de45dd699f3cc08
!pip install ./

Processing /content/drive/MyDrive/ai4bharatIndicwav2vec/fairseq
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 104.0/104.0 kB 4.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 123.8/123.8 kB 4.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 278.3/278.3 kB 5.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 112.4/112.4 kB 5.5 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for fairseq: filename=fairseq-0.12.2-cp310-cp310-linux_x86_64.whl size=20432086 sha256=69a097afe8a164cbd742c0fa2cd5548515ebcd661c2f6bd1de5d266884629e9a
  Stored in directory: /tmp/pip-ephem-wheel-cache-396klom0/wheels/6f/25/38/c07b391264079238d6477e9e9487d783035b505281a980ffc5
  Created wheel for antlr4-python3-runtime: filename=antlr4_python3_runtime-4.8-py3-none-any.whl size=141214 sha256=44efcefe976a50bea74f33

In [ ]:
%cd ..

/content/drive/MyDrive/ai4bharatIndicwav2vec


In [ ]:
!pwd

/content/drive/MyDrive/ai4bharatIndicwav2vec


In [ ]:
#!curl -O https://indic-asr-public.objectstore.e2enetworks.net/aaai_ckpts/models/bn/bn.pt


  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 3611M  100 3611M    0     0  57.9M      0  0:01:02  0:01:02 --:--:-- 61.1M


In [ ]:
#!curl -O https://indic-asr-public.objectstore.e2enetworks.net/aaai_ckpts/pretrained_models/indicw2v_large_pretrained.pt

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 3632M  100 3632M    0     0  58.3M      0  0:01:02  0:01:02 --:--:-- 57.2M


In [ ]:
import os
os.environ['HYDRA_FULL_ERROR'] = '1'

In [ ]:
!echo $HYDRA_FULL_ERROR

1


In [ ]:
!git clone https://github.com/pytorch/fairseq.git
%cd fairseq
!git checkout cf8ff8c3c5242e6e71e8feb40de45dd699f3cc08
!pip install pip==23.0.1
!pip install ./
%cd /content/drive/MyDrive/ai4bharatIndicwav2vec
!pip install "numpy<1.24"

Cloning into 'fairseq'...
remote: Enumerating objects: 35385, done.
remote: Counting objects: 100% (48/48), done.
remote: Compressing objects: 100% (36/36), done.
remote: Total 35385 (delta 10), reused 40 (delta 9), pack-reused 35337 (from 1)
Receiving objects: 100% (35385/35385), 25.47 MiB | 31.09 MiB/s, done.
Resolving deltas: 100% (25538/25538), done.
/content/fairseq
Note: switching to 'cf8ff8c3c5242e6e71e8feb40de45dd699f3cc08'.

You are in 'detached HEAD' state. You can look around, make experimental
changes and commit them, and you can discard any commits you make in this
state without impacting any branches by switching back to a branch.

If you want to create a new branch to retain commits you create, you may
do so (now or later) by using -c with the switch command. Example:

  git switch -c <new-branch-name>

Or undo this operation with:

  git switch -

Turn off this advice by setting config variable advice.detachedHead to false

HEAD is now at cf8ff8c3 Add unittests for jitt

In [ ]:
!pip install wandb

In [ ]:
!pip install tensorboardX

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 101.7/101.7 kB 2.9 MB/s eta 0:00:00


In [ ]:
!wandb login

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit: 
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


In [ ]:
%cd /content/

/content


In [ ]:
# !fairseq-hydra-train task.data=${PWD}"/workshop-2022/asr_data/noa_training_1hr/manifest/hindi" \
#     dataset.max_tokens=200000 \
#     common.log_interval=20 \
#     model.freeze_finetune_updates=1000 \
#     model.w2v_path=${PWD}"/workshop-2022/models/checkpoint_ft.pt" \
#     checkpoint.save_dir=${PWD}"/workshop-2022/models/indicwav2vec_noa" \
#     checkpoint.restore_file=${PWD}"/workshop-2022/models/hi_mucs_dc.pt" \
#     distributed_training.distributed_world_size=1 \
#     +optimization.update_freq='[1]' \
#     +optimization.lr=[0.0001] \
#     optimization.max_update=100000 \
#     checkpoint.save_interval_updates=10000 \
#     --config-dir ${PWD}"/finetune_configs" \
#     --config-name ai4b_xlsr

In [ ]:
!pwd

/content


In [ ]:
!rm -rf outputs

In [ ]:
!pwd

/content


In [ ]:
!fairseq-hydra-train +task.data="/content/drive/MyDrive/ai4bharatIndicwav2vec/mucs/bengali/manifest" \
    common.wandb_project="sylheti" \
    model.w2v_path="/content/drive/MyDrive/ai4bharatIndicwav2vec/indicw2v_large_pretrained.pt" \
    common.log_interval=50 \
    common.log_format=tqdm \
    dataset.max_tokens=1000000 \
    checkpoint.save_dir="/content/outputs3/" \
    checkpoint.restore_file="/content/drive/MyDrive/ai4bharatIndicwav2vec/outputs1/outputs1/checkpoint_best.pt" \
    +optimization.update_freq="[1]" \
    +optimization.lr=[0.0001] \
    distributed_training.distributed_world_size=1 \
    --config-dir /content/drive/MyDrive/ai4bharatIndicwav2vec/configs \
    --config-name ai4b_xlsr_2

Streaming output truncated to the last 5000 lines.
epoch 112 | valid on 'valid' subset:  48% 88/183 [00:35<00:31,  3.06it/s]
epoch 112 | valid on 'valid' subset:  49% 89/183 [00:35<00:30,  3.05it/s]
epoch 112 | valid on 'valid' subset:  49% 90/183 [00:35<00:30,  3.04it/s]
epoch 112 | valid on 'valid' subset:  50% 91/183 [00:36<00:29,  3.13it/s]
epoch 112 | valid on 'valid' subset:  50% 92/183 [00:36<00:28,  3.16it/s]
epoch 112 | valid on 'valid' subset:  51% 93/183 [00:36<00:28,  3.19it/s]
epoch 112 | valid on 'valid' subset:  51% 94/183 [00:37<00:27,  3.20it/s]
epoch 112 | valid on 'valid' subset:  52% 95/183 [00:37<00:27,  3.18it/s]
epoch 112 | valid on 'valid' subset:  52% 96/183 [00:37<00:27,  3.13it/s]
epoch 112 | valid on 'valid' subset:  53% 97/183 [00:38<00:27,  3.11it/s]
epoch 112 | valid on 'valid' subset:  54% 98/183 [00:38<00:27,  3.06it/s]
epoch 112 | valid on 'valid' subset:  54% 99/183 [00:38<00:26,  3.17it/s]
epoch 112 | valid on 'valid' subset:  55% 100/183 [00:39<00:2

In [ ]:
%cp -r /content/outputs3/ /content/drive/MyDrive/ai4bharatIndicwav2vec/outputs3

In [ ]:
!rm -rf /content/outputs3 /content/outputs/

In [ ]:
#!fairseq-hydra-train +task.data="/content/drive/MyDrive/ai4bharatIndicwav2vec/mucs/bengali/manifest" \
#   common.wandb_project="sylheti" \
#   model.w2v_path="/content/drive/MyDrive/ai4bharatIndicwav2vec/indicw2v_large_pretrained.pt" \
#   common.log_interval=50 \
#   common.log_format=tqdm \
#   dataset.max_tokens=1000000 \
#   checkpoint.save_dir="./" \
#   +optimization.update_freq="[1]" \
#   distributed_training.distributed_world_size=1 \
#   --config-dir /content/drive/MyDrive/ai4bharatIndicwav2vec/configs \
#   --config-name ai4b_xlsr

Streaming output truncated to the last 5000 lines.
epoch 041 | valid on 'valid' subset:  95% 172/182 [00:49<00:03,  3.32it/s]
epoch 041 | valid on 'valid' subset:  95% 173/182 [00:49<00:02,  3.29it/s]
epoch 041 | valid on 'valid' subset:  96% 174/182 [00:49<00:02,  3.28it/s]
epoch 041 | valid on 'valid' subset:  96% 175/182 [00:50<00:02,  3.30it/s]
epoch 041 | valid on 'valid' subset:  97% 176/182 [00:50<00:01,  3.41it/s]
epoch 041 | valid on 'valid' subset:  97% 177/182 [00:50<00:01,  3.39it/s]
epoch 041 | valid on 'valid' subset:  98% 178/182 [00:51<00:01,  3.45it/s]
epoch 041 | valid on 'valid' subset:  98% 179/182 [00:51<00:00,  3.49it/s]
epoch 041 | valid on 'valid' subset:  99% 180/182 [00:51<00:00,  3.58it/s]
epoch 041 | valid on 'valid' subset:  99% 181/182 [00:51<00:00,  3.54it/s]
epoch 041 | valid on 'valid' subset: 100% 182/182 [00:52<00:00,  3.72it/s]
                                                                          [2024-10-24 15:24:57,211][valid][INFO] - epoch 041